# CLIMADA coding conventions

## Dependencies (python packages) 

Python is extremely powerful thanks to the large amount of available libraries, packages and modules. However, maintaining a code with a large number of such packages creates dependencies which is very care intensive. Indeed, each package developer can and does update and develop continuously. This means that certain code can become obsolete over time, stop working altogether, or become incompatible with other packages. Hence, it is crucial to keep the philosophy:

*As many packages as needed, as few as possible.*

Thus, when you are coding, follow these priorities:

1. [Python standard library](https://docs.python.org/3/library/index.html)
2. Functions and methods already implemented in CLIMADA (do NOT introduce circulary imports though)
3. [Packages already included in CLIMADA](https://github.com/CLIMADA-project/climada_python/network/dependencies)
4. Before adding a new dependency: 
    - Contact a [repository admin](https://github.com/CLIMADA-project/climada_python/wiki/Developer-Board) to get permission
    - Open an [issue](https://github.com/CLIMADA-project/climada_python/issues)
    
Hence, first try to solve your problem with the standard library and function/methods already implemented in CLIMADA (see in particular the [utility functions](#Utility-functions)) then use the packages included in CLIMADA, and if this is not enough, propose the addition of a new package. Do not hesitate to propose new packages if this is needed for your work!

## Class inheritance 

In Python, a [class can inherit from other classes](https://docs.python.org/3/tutorial/classes.html), which is a very useful mechanism in certain circumstances. However, it is wise to think about inheritance before implementing it. Very important, is that CLIMADA classes do not inherit from external library classes. For example, Exposure directly inherited from Geopandas. This caused problems in CLIMADA when the package Geopandas was updated.

**CLIMADA classes shall NOT inherit classes from external modules.**

## Paper repository 

Applications made with CLIMADA which are published in the form of a paper or a report are very much encouraged to be submitted to the [climada/paper](https://github.com/CLIMADA-project/climada_papers) repository. You can either:

- Prepare a well-commented jupyter notebook with the code necessary to reproduce your results and upload it to the [climada/paper](https://github.com/CLIMADA-project/climada_papers) repository. Note however that the repository cannot be used for storing data files.
- Upload the code necessary to reproduce your results to a separate repository of your own. Then, add a link to your repository and to your publication to the readme file on the [climada/paper](https://github.com/CLIMADA-project/climada_papers) repository.

**Notes about DOI**

Some journals require you to provide a DOI to the code and data used for your publication. In this case, we encourage you to create a separate repository for your code and create a DOI using [Zenodo](https://zenodo.org/) or any specific service from your institution (e.g. [ETH Zürich](https://documentation.library.ethz.ch/display/DOID/DOI+Registration+Manual)).

The CLIMADA releases are also identified with a DOI.

## Utility functions

In CLIMADA, there is a set of utility functions defined in `climada.util`. A few examples are:

- convert large monetary numbers into thousands, millions or billions together with the correct unit name
- compute distances
- load hdf5 files
- convert iso country numbers between formats
- ...

Whenever you develop a module or make a code review, be attentive to see whether a given functionality has already been implemented as a utility function. In addition, think carefully whether a given function/method does belong in its module or is actually independent of any particular module and should be defined as a utility function.

It is very important to not reinvent the wheel and to avoid unnecessary redundancies in the code. This makes maintenance and debugging very tedious.


## Data dependencies

### Web APIs
CLIMADA relies on open data available through web APIs such as those of the World Bank, Natural Earth, NASA and NOAA.
You might execute the test ``climada_python-x.y.z/test_data_api.py`` to check that all the APIs used are active.
If any is out of service (temporarily or permanently), the test will indicate which one.

### Manual download

As indicated in the software and tutorials, other data might need to be downloaded manually by the user. The following table shows these last data sources, their version used, its current availability and where they are used within CLIMADA:

| Name                                            | Version | Link | CLIMADA class | CLIMADA version | CLIMADA tutorial reference    |
|-------------------------------------------------|---------|------|---------------|-----------------|-------------------------------|
| Fire Information for Resource Management System |         |[FIRMS](https://firms.modaps.eosdis.nasa.gov/download/) | BushFire      | > v1.2.5          | climada_hazard_BushFire.ipynb |
| Gridded Population of the World (GPW)           | v4.11   |[GPW4.11](https://sedac.ciesin.columbia.edu/data/set/gpw-v4-population-count-rev11)     | LitPop        | > v1.2.3        | climada_entity_LitPop.ipynb   |


## Side note on parameters

### Don't use *args and **kwargs parameters without a very good reason.

There _are_ valid use cases for [this kind of parameter notation](https://realpython.com/python-kwargs-and-args/).\
In particular `*args` comes in handy when there is an unknown number of equal typed arguments to be passed. E.g., the `pathlib.Path` constructor.\
But if the parameters are expected to be structured in any way, it is just a bad idea.

In [2]:
def f(x, y, z):
    return x + y + z

# bad in most cases
def g(*args, **kwargs):
    x = args[0]
    y = kwargs['y']
    s = f(*args, **kwargs)
    print(x, y, s)

g(1,y=2,z=3)

1 2 6


In [3]:
# usually just fine
def g(x, y, z):
    s = f(x, y, z)
    print(x, y, s)

g(1,y=2,z=3)

1 2 6


### Decrease the number of parameters.

Though CLIMADA's pylint configuration .pylintrc allows 7 arguments for any method or function before it complains, it is advisable to aim for less.
It is quite likely that a function with so many parameters has an inherent design flaw.

There are very well designed command line tools with inumerable optional arguments, e.g., rsync - but these are command line tools. There are also methods like `pandas.DataFrame.plot()` with countless optional arguments and it makes perfectly sense.

But within the climada package it probably doesn't.
divide et impera!

Whenever a method has more than 5 parameters, it is more than likely that it can be refactored pretty easily into two or more methods with less parameters and less complexity:


In [2]:
def f(a, b, c, d, e, f, g, h):
    print(f'f does many things with a lot of arguments: {a, b, c, d, e, f, g, h}')
    return sum([a, b, c, d, e, f, g, h])

f(1, 2, 3, 4, 5, 6, 7, 8)

f does many things with a lot of arguments: (1, 2, 3, 4, 5, 6, 7, 8)


36

In [3]:
def f1(a, b, c, d):
    print(f'f1 does less things with fewer arguments: {a, b, c, d}')
    return sum([a, b, c, d])

def f2(e, f, g, h):
    print(f'f2 dito: {e, f, g, h}')
    return sum([e, f, g, h])

def f3(x, y):
    print(f'f3 dito, but on a higher level: {x, y}')
    return sum([x, y])

f3(f1(1, 2, 3, 4), f2(5, 6, 7, 8))

f1 does less things with fewer arguments: (1, 2, 3, 4)
f2 dito: (5, 6, 7, 8)
f3 dito, but on a higher level: (10, 26)


36

This of course pleads the case on a strictly formal level. No real complexities have been reduced during the making of this example.\
Nevertheless there is the benefit of reduced test case requirements. And in real life, real complexity _will_ be reduced.